# Title
[]()

In [1]:
from pandas import json_normalize  
import pandas as pd
import sys
sys.path.append(r"C:\Users\silvh\OneDrive\lighthouse\custom_python")
sys.path.append(r"C:\Users\silvh\OneDrive\lighthouse\portfolio-projects\online-PT-social-media-NLP\src")
from silvhua import *
from datetime import datetime
# import json
# from plotly.subplots import make_subplots
# import requests

In [2]:

sys.path.append(r"C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\src")
from summarization import Chatbot, reply, batch_reply

In [3]:
from article_processing import create_text_dict

In [38]:
# set the option to wrap text within cells
pd.set_option('display.max_colwidth', None)
# pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)

In [4]:
# from pypdf import PdfReader
import pandas as pd
import openai
import os
from openai.embeddings_utils import get_embedding, cosine_similarity
import re

# `batch_summarize`

In [21]:
def batch_summarize(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df['prompt'].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                temp_qna_dict[key][index], chatbot_dict[f'{iteration_id}_text{key}_prompt{index}'] = reply(input, text)
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

# `batch_reply2`

In [52]:
def batch_reply2(text, prompts_df, qna_dict,  chatbot_dict, iteration_id, prompt_column='prompt',
    save_outputs=False, append_version=True,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Send multiple summarization prompts to ChatGPT for the same text.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    qna_dict[iteration_id] = dict()
    prompts_df = prompts_df.reset_index(drop=True)

    for index, input in prompts_df['prompt'].items():
        # print(input)
        try:
            # prompt_num = index+1
            print(f'**Prompt #{index} of {len(prompts_df)}**')
            qna_dict[iteration_id][index], chatbot_dict[f'{iteration_id}_prompt{index}'] = reply(input, text)
        except:
            print('Error making chatbot request')
            break
    try:
        updated_qna_dict = pd.concat([
            pd.DataFrame(qna_dict[iteration_id]),
            prompts_df.transpose()
        ])
        qna_dict[iteration_id] = updated_qna_dict
        if save_outputs:
            try:
                filename = f"prompt_experiments_{qna_dict[iteration_id].loc['article_title', 1]}"
                savepickle(updated_qna_dict, filename=filename, path=pickle_path, append_version=append_version)
                save_csv(updated_qna_dict, filename=filename, path=pickle_path, append_version=append_version)
            except:
                print('Unable to save outputs')
        # return updated_qna_dict, chatbot_dict
    except:
        print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

# Create text dictionary

In [171]:
text1 = """Higher muscle fiber conduction velocity and early rate of torque development in chronically strength-trained individuals
DISCUSSION
MFCV was measured during explosive force contractions in a group of resistance-trained individuals and a control cohort. ST exhibited greater explosive torque, early RTD, and greater MFCV with respect to controls throughout the contraction. When explosive torque was normalized to maximal torque, ST had a higher RTD at the beginning of the contraction (0–50 ms). Moreover, a greater absolute and normalized conduction velocity (MFCVMAX) during the EMD and in the first 50 ms of torque generation was observed for the ST group. This result indicates a recruitment of motor units with greater conduction velocities. This is the first study showing that ST may recruit larger motor units in a shorter amount of time.

Muscle Fiber Conduction Velocity
The average MFCV values are in agreement with previous reports of MFCV during steady-state contractions. For example, Farina et al. reported estimates of MFCV in the BB during isometric steady-state contractions at 50% MVC of ~4.6 m/s (30). Zwarts and Arendt-Nielsen estimated MFCV at high contraction forces of the BB and reported values ranging between 3.22 and 5.11 m/s (57). MFCV average values in the present study were also in agreement with estimates of single-motor unit conduction velocities using intramuscular EMG recordings during voluntary and electrical activation of the BB muscle. Moreover, the present estimates are also in accordance with other studies involving different muscular contractions and protocols (25, 26, 32, 41, 42, 47, 48).

Interestingly, only two studies assessed MFCV in power athletes and only during electrical stimulation and maximal voluntary contractions (43, 49). Sadoyama et al. reported a significantly higher maximal MFCV in a group of trained sprinters compared with endurance runners (4.84 vs. 4.31 m/s; 49). Moreover, they reported a significant relation between the relative area of fast-twitch fibers and conduction velocity (49).

Recently, Methenitis et al. estimated MFCV during electrical stimulation of muscle fibers in endurance runners and power-trained and ST individuals and separately measured RTD (43). They reported significant relations between MFCV, muscle fiber cross-sectional area, and rate of force development (43). However, estimates of MFCV were assessed during electrical stimulation and thus separately from the voluntary generation of explosive force. Therefore, it was not possible to associate the underlying neural strategies of muscle control with explosive force performance. Collectively, these previous results indicate that MFCV may be an indicator of muscle explosive performance, although no previous study assessed MFCV during explosive torque generation.

Explosive Torque and RTD
The RTD was significantly greater for ST during the early phase of explosive torque generation (Fig. 3A). However, when the moment-time curve was normalized to the maximal strength, the RTD for the resistance-trained subjects was significantly different only in the first 50 ms of the contraction (Fig. 3B). Because the relative explosive torque at 150 and 200 ms from contraction onset was similar between the two groups, the controls developed higher RTD during the second and third time windows from force onset (Fig. 3B).

Previous studies found an increase in the EMG amplitude and rate of force development in the initial phase of contraction after 4 wk of explosive training (7). In addition, a greater normalized rate of force development in the first 50 ms of contraction was found for power athletes during knee extensor explosive torque (51). Because the first 50 ms of contraction strongly reflect neural activation (13, 15, 16, 54), strength or power training presumably increases RTD by a faster recruitment of motor units, as discussed below.

MFCV During the Explosive Phase of Contraction
ST individuals have the ability to develop higher levels of force in the first 50 ms of contraction. This seems to be associated with greater MFCV in the same time interval, which indicates recruitment of motor units with greater conduction velocity. The role of motor unit recruitment during explosive force contraction is not well understood because it is not possible to identify representative populations of motor units in very short time intervals.

The primary determinant of motor unit twitch force is the number of muscle fibers innervated by the axon (17, 53). Motor unit peak twitch forces in humans range from ~6 to ~78 mN·m with maximal tetanic forces ranging from ~30 to ~200 mN·m (36, 38). Therefore, one of the mechanisms that determined the increase in RTD during the first 0–50-ms interval in the ST may have been the recruitment of larger motor units with greater and faster twitches. There is evidence showing correlations between electrically evoked twitch torque and early voluntary rate of force development, which could be associated with the differences in muscle fiber composition and/or Ca2+ saturation for the trained individuals (3, 34).

Interestingly, the two groups showed similar EMD values, which is in accordance with a previous study that compared the EMD in power-trained and untrained cohorts (51). This finding is, however, contradictory with a higher MFCV during the EMD. A higher absolute MFCV value should theoretically anticipate the release of Ca2+ and thus the rise in force. However, these problems may be related to the techniques employed in assessing the delay between the neural and muscular apparatus. The EMD during explosive contractions may not be sensitive to differences in neural activation due to a compressed recruitment (12, 15). We have recently shown that when the EMD is assessed as the time difference between the neural drive and force during the sustained contractions, the central nervous system modulates the delay broadly and according to the rate of force development (12). Indeed, the neuromechanical delay seems to be predominantly influenced by the type of recruited motor units and the intrinsic properties of the motor neuron (5, 12). Future studies assessing the neuromechanical delay in strength/power-trained individuals may be warranted.

MFCV increases with voluntary force production due to the relation between motor unit recruitment thresholds and fiber diameter (4, 8, 11, 35). This association implies that the ordered recruitment of motor units may be assessed by estimates of conduction velocity (10). We have recently reported that large, high-threshold motor units innervate fibers with large diameter (11), which explains the association between motor unit mechanical properties and conduction velocity previously reported (4). Moreover, we have recently demonstrated that the increase in average MFCV during voluntary force contractions is associated with the progressive recruitment of motor units with increasing conduction velocity and predicts recruitment thresholds at the individual subject level (10).

In the present study, MFCV was the average of the conduction velocities of the active motor units during explosive force contractions, in time intervals of 50 ms following EMG onset. We showed that there may be significant differences in the recruited motor units during explosive tasks in ST compared with moderately active individuals. Absolute MFCV values were greater in ST throughout the full duration of the explosive contractions (Fig. 3A). Moreover, the early absolute and normalized MFCV were positively associated with RTD (Fig. 4). Because absolute MFCV values are linearly related to the diameters of muscle fibers, higher absolute conduction velocity values may indicate that ST have muscle fibers with larger diameters due to the strength training-induced hypertrophy (43) compared with controls (24, 43).

However, when MFCV values were normalized to the maximal value during MVF (full motor unit recruitment), ST had a significantly greater MFCV-rel during the initial phase of the explosive contractions. Specifically, MFCV-relEMD and MFCV-rel0–50 were on average ~9% greater (Fig. 4B). This suggests that during the early phase of explosive force, ST have the ability to recruit motor units with faster conduction velocities in a shorter time. It takes ~100 ms more for the controls to reach similar values of normalized MFCV compared with the ST group. Interestingly, the changes in conduction velocity did not differ between groups (Fig. 4, A and B), and the MFCV plateaued in the interval 50–100 ms, which can be interpreted as full motor unit recruitment (10). This interpretation is in agreement with previous studies reporting that most motor units are recruited at one-third of maximal force during explosive contractions (15, 16). Moreover, MFCV increased in all subjects from the EMD to 0–50 ms, indicating that the ordered recruitment according to the size of the motor unit was preserved during the explosive tasks in both groups.

The underlying mechanism that may determine an increase in explosive force for the ST individuals may be an anticipated recruitment of high-threshold motor units with high conduction velocities. The difference between MFCV of high- and low-threshold motor units within a muscle is ~2 m/s (11). A faster motor unit recruitment (and conduction velocity) would achieve greater peak mechanical torques in a shorter time. The release of calcium from the sarcoplasmic reticulum is correlated to the speed of the action potential on the fiber membrane (21). Indeed, MFCV is related to motor unit time-to-peak twitch forces (4). The increase in MFCV may potentially allow a faster calcium uptake and thus anticipating the rise in force.

Van Cutsem et al. reported an increase in motor unit discharge rates following ballistic training (55) and concluded, in agreement with other studies, that RTD depends on motor unit discharge rate (16, 18, 55). On the other hand, the recruitment threshold of motor units significantly influences the discharge rate at a given absolute force (18). Anticipating the recruitment of high-threshold motor units would result in reaching motor unit peak discharge rate and motor unit peak RTD in a shorter time. Accordingly, in the present study, MFCV was positively associated with RTD (Fig. 4A), suggesting that motor unit recruitment may play an important role in explosive force production.

Interestingly, the correlation between RTD0–50 and early MFCV values (MFCVEMD,0–50) was different for the ST and untrained individuals. MFCV0–50 was not correlated with RTD0–50 in the ST group (Fig. 4). This result indicates that ST completed the motor unit recruitment during the very early phase of explosive force, i.e., between the EMD and the first 50 ms from contraction onset (Fig. 4B). The increase in MFCV during the explosive force at the 50- and 100-ms time points for the ST is presumably due to some subjects continuing the recruitment while the subjects with higher RTD achieved a faster plateau in MFCV (Fig. 4). Indeed, it took more time for the untrained individuals to reach high MFCV (and full motor unit recruitment) values (Figs. 3 and 4).

It must be noted that the number of subjects in the present study may be too low for a correlation study. Moreover, the cross-sectional design cannot isolate the innate and environmental factors that contributed to the explosive force and MFCV differences found between the cohorts. However, in the present study the trained individuals performed combined strength and explosive training for >3 yr. Recent evidence showed a significant increase in explosive force production after 12 wk of isometric explosive training compared with isometric sustained-contraction strength training (6). The large differences in the early RTD for the trained subjects in the present study may also indicate that the neural contributors to explosive strength could be related to chronic exposure to explosive/strength training and that the neural adaptations may continue over time. Future studies assessing the neural contributors to explosive force in large cohorts and longitudinal (>1 yr) interventions are warranted.

Conclusion
Resistance-trained individuals showed higher RTD and explosive force in the very early phase of contraction that was accompanied by an increase in absolute and normalized MFCV compared with controls. These observations may be explained by recruitment of fast-twitch motor units (i.e., large motor units with large muscle fiber diameters) in a shorter amount of time in the resistance-trained cohort than in controls. In addition to the functional implications in the study of human explosive force, the study also presents a methodology that may be applied in the assessment of the neural strategies of muscle control in health, training, and pathology.
"""
text2 = """Homeostatic and non-homeostatic appetite control along the spectrum of physical activity levels an updated perspective

284 5. The impact of physical activity and exercise on the mechanisms of appetite control 
285 Emerging studies are shedding light on the mechanisms contributing to the proposed 
286 dysregulation of appetite at lower levels of PA and more sensitive appetite control at higher 
287 levels of PA. These mechanisms may not necessarily be the same along the whole spectrum 
288 of PA levels. Acutely, exercise has been shown to influence gastric emptying [78], attenuate 
289 the release of ghrelin and increase the secretion of PYY, GLP-1 and pancreatic polypeptide 
290 [79]. Chronic exercise may increase the postprandial secretion of GLP-1 and PYY [80]. 
291 Therefore, habitual PA (and exercise) may interact with food intake to enhance hormonal 
292 satiety signalling [81]. Moreover, regular PA and exercise training are associated with several 
293 other physiological adaptations such as improved sensitivity to insulin [82] and leptin [83, 84], 
294 substrate metabolism [85], and body composition [86], which have been proposed as 
295 mechanisms involved in food intake and eating behaviour [87, 88]. Evidence suggests that PA 
296 influences appetite control through a dual-process action which increases the drive to eat but 
297 also post-meal satiety [89]. Several studies have now demonstrated that physically active 
298 individuals show better energy compensation than their less active counterparts following 
299 consumption of preloads differing in energy content such that they reduce EI to offset the 
300 difference in energy consumed from the preloads [10, 90-94]. This preload-test meal paradigm 
301 is effective in measuring the strength of satiety [95]. These improvements in satiety may be 
302 associated with exercise-induced adaptations in episodic satiety signalling [80, 91, 96] or
303 gastric emptying [97]. In contrast, we have shown that satiation does not appear to be 
14
304 influenced by PA level in non-obese individuals when measured with a passive 
305 overconsumption paradigm comparing ad libitum EI at meals high in fat or carbohydrate [9]. 
306 However, in overweight and obese individuals, Caudwell et al. [1] showed that exercise 
307 training led to a reduction in EI at a high-fat/energy dense test meal. This may be associated 
308 with enhanced satiation, but given the homeostatic and non-homeostatic determinants of food 
309 intake, may also reflect changes in food hedonics or behavioural traits. 
310 While there is strong support that habitual PA affects homeostatic mechanisms 
311 controlling food intake, less is known on its effect on non-homeostatic processes, and their 
312 contribution to appetite control along the spectrum of PA levels. Indeed, secondary analyses 
313 from the study from Caudwell et al. [1] revealed a reduction in hedonic wanting for high-fat 
314 foods relative to low-fat foods (Leeds Food Preference Questionnaire), disinhibition and binge 
315 eating following exercise training [Beaulieu et al., unpublished results]. Furthermore, another 
316 study from our group found inverse associations between time spent in MVPA and disinhibition 
317 and binge eating, but these did not remain significant after controlling for body fat [24]. This 
318 corroborates a study by Shook et al. who found greater disinhibition in their lowest quintile of 
319 MVPA but not when controlling for body weight [77], and the aforementioned reduction in 
320 disinhibition and binge eating score following 12 weeks of exercise training which did not 
321 remain significant after controlling for change in body fat [Beaulieu et al., unpublished results]. 
322 These differences in disinhibition and binge eating were not apparent in non-obese individuals 
323 varying in PA levels [9, 10], suggesting the influence of habitual PA on eating behaviour traits 
324 may be more strongly influenced by body composition. In terms of food hedonics, differences 
325 in the rewarding value of foods (liking and wanting) have been observed in lean active 
326 compared to overweight inactive males [98], but in non-obese individuals, PA level did not 
327 influence liking and wanting for high-fat food in the hungry or fed states [9, 10]. In inactive 
328 individuals with overweight and obesity, 12 weeks of exercise training (125-250 kcal per 
329 exercise session) did not affect liking or wanting [99], whereas another 12-week intervention 
330 at a higher dose of exercise (500 kcal per exercise session) reduced the hedonic wanting for 
15
331 high-fat food independent of changes in body fat [Beaulieu et al. unpublished results]. 
332 Moreover, habitual (self-reported) PA may differently impact food cravings depending on 
333 exercise type and sex [100]. These studies suggest there may be differing effects of PA on
334 non-homeostatic appetite control according to an individual’s body fat status, sex, and dose 
335 and type of PA. 
336 Therefore, we can propose that in addition to individuals with non-regulated appetite 
337 having blunted satiety signalling, excess body fat in these individuals may amplify non 338 homeostatic inputs favouring overconsumption. In contrast, individuals with regulated appetite 
339 with higher levels of PA have enhanced postprandial sensitivity, allowing for EI to be better 
340 matched to EE in response to hunger and satiety signals. This is demonstrated in an updated 
341 perspective of the zones of appetite control in Figure 3.

350 6. Interaction between physical activity and diet composition on energy intake and 
351 energy balance 
352 While PA appears to affect several mechanisms of appetite control, as described 
353 above, whether it renders individuals less susceptible to overconsumption in the current 
354 obesogenic food environment has not been extensively examined. This is important to 
355 consider, with headlines stating “You cannot outrun a bad diet” [101]. Only a few studies have 
356 investigated the impact of PA and diet composition on EI and energy balance. A study by 
357 Tremblay et al. [102] in males found that consumption of a high-fat diet over two days following 
358 a 500-kcal exercise bout led to a positive energy balance, whereas consumption of a low-fat 
359 diet was able to maintain the energy deficit produced by exercise. Along those lines, 
360 Murgatroyd et al. [103] showed in males that increasing the dietary fat content (and energy 
361 density) of an ad libitum diet in a day where exercise was imposed (~675 kcal) increased EI 
362 and led to a positive energy balance (albeit not statistically significant). Moreover, consumption 
363 of a high-fat diet while imposing inactivity resulted in a daily positive energy balance of 
364 approximately 1000 kcal more than with imposed exercise, and 1200 kcal more than with 
365 exercise on a low-fat diet. Other studies in males [104] and females [105] corroborated these 
366 findings by demonstrating that the consumption of a high-fat meal following an exercise bout 
367 resulted in significantly greater relative EI (after considering the EE of the exercise) compared 
368 with a low-fat meal. Interestingly, palatability of both high-fat and low-fat meals increased after 
369 exercise compared to rest in females, but not in males [105]. These studies highlight the 
370 potency of the phenomenon of passive overconsumption. Therefore, the degree of 
371 compensation observed in response to PAEE can readily be modulated simply by altering the
372 energy density of the diet and proposals about compensation need to be interpreted with care. 
17
373 Whether being habitually physically active enhances the response to dietary 
374 manipulations is also of interest. As discussed above, we have shown that physically active 
375 individuals are also prone to acute passive overconsumption with an imposed high-fat meal 
376 [9]. In addition, while individuals with higher levels of PA were found to be sensitive to the 
377 acute nutritional manipulation of preloads varying in energy content by reducing EI at the 
378 following meal, objectively-measured daily EI (including the preload) was greater after a high 379 energy relative to a low-energy preload regardless of PA level, demonstrating an effect of 
380 passive overconsumption [10]. Others have shown that active individuals may compensate 
381 beyond the immediate meal following intake of a high-energy preload, attenuating the risk of 
382 overconsumption, but this was measured with food records and daily EI including the preload 
383 was not reported [90, 91, 93]. The long-term compensatory response to high energy density 
384 food consumption in physically active individuals is unknown. The EE associated with PA may 
385 be helpful in mitigating episodes of overconsumption and fluctuations in EI over time [106, 
386 107]. However, given the available evidence, in the general population, higher levels of 
387 habitual PA in conjunction with a diet lower in energy density appear to be optimal for appetite 
388 control and energy balance. 
389
390 7. Implications and future directions 
391 The impact of PA on the mechanisms of appetite control has implications for individuals 
392 wishing to lose fat mass through exercise as large variability in the individual response to 
393 exercise interventions have been observed [89, 108]. These varying responses in fat loss to 
394 exercise training suggest that some individuals compensate for the increase in PA (and EE) 
395 through greater food intake or other mechanisms impacting on energy balance, minimizing 
396 the effect of exercise on fat loss. In both those susceptible and resistant to exercise-induced 
397 weight loss, hunger and the strength of satiety were enhanced with exercise training, showing 
398 a robust effect of the dual-process action of PA on appetite control; however, the increase in 
18
399 hunger was greater in those resistant to weight loss [89]. The compensatory adaptations in 
400 appetite control and eating behaviour following exercise-induced weight loss are beyond the 
401 scope of this review and have been reviewed elsewhere [20, 109, 110]. Nevertheless, it should 
402 be acknowledged that certain baseline (pre-intervention) characteristics of appetite may 
403 predict the susceptibility to exercise-induced weight loss such as the hedonic response to 
404 acute exercise [111] and the peptide response to food consumption [112], which is of interest 
405 for future research to help personalise interventions to promote successful fat loss with 
406 exercise. 
407 The role of PAEE in driving EI is important for future research to clarify as it can make 
408 up a significant proportion of TDEE in physically active individuals (see Figure 1) [113]. While 
409 the influence of PA on some processes of appetite appear to be independent of body fat, more 
410 research is required to understand the role of body composition and body fat status in the 
411 relationship between PA level and appetite control. We have reported above that PA (or 
412 factors associated with PA) may moderate the relationship between fat mass and EI, which is 
413 an interesting avenue for future research. Other potential moderators of the relationship 
414 between PA and appetite that remain to be examined further include sex [114] and age [93]. 
415 Additionally, very little is known on how the type, dose, intensity and timing of habitual PA and 
416 exercise affect homeostatic and non-homeostatic appetite. The mechanisms responsible for 
417 the apparent enhancement in the satiety response to food consumption in physically active
418 individuals also remain to be fully elucidated. Finally, in light of the research on the interaction 
419 between PA and dietary manipulations, it is important for future research to take an energy 
420 balance perspective [115] to increase our understanding of the complex relationships and 
421 interactions among PA, diet composition, body composition and appetite control along the 
422 spectrum of PA levels. 
423
424 8. Summary 
19
425 Food intake is modulated by several homeostatic and non-homeostatic mechanisms 
426 controlling appetite. Evidence is accumulating to support the view that EI along the spectrum 
427 of PA is J-shaped, with individuals with low levels of PA being in a non-regulated zone of 
428 appetite whereas those with higher levels of PA operating in a regulated zone with more 
429 sensitive appetite control. Body fat also varies along the spectrum of PA and may impact the 
430 sensitivity of satiety signals and non-homeostatic inputs (food hedonics and behavioural traits) 
431 favouring overconsumption at lower levels of PA, but this remains to be fully understood. PA
432 affects the homeostatic mechanisms of appetite via a proposed dual-process action of
433 increased drive to eat from greater EE, but also by enhanced satiety response to food, likely 
434 through more sensitive postprandial signalling. An important tenet of our current position is 
435 that PAEE is a determinant of EI (although with greater variability than RMR). These 
436 processes generate a better adjustment of EI to EE in response to hunger and satiety signals 
437 at higher levels of PA. However, special attention needs to be given to diet composition, with 
438 a high-fat energy-dense diet leading to acute passive overconsumption of energy along the 
439 entire spectrum of PA. Importantly, the strength of the various mechanisms and determinants 
440 of appetite will vary between individuals along the spectrum of PA, highlighting the need to 
441 recognise that the impact of PA on appetite control is not a case of ‘one size fits all’.

"""
text_dict = create_text_dict([text1, text2])
text_dict.keys()

dict_keys([1, 2])

# Experiment 1

## Create prompts_df

In [16]:
from itertools import product
prompts_dict = dict()
experiment_num = 1

prep_step = [
    # "Take the key points to",
    # "Take the key points and numerical descriptors to",
    ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    "lay audience",
    # ""
    # "seniors"
]
task_part2 = [
    # "",
    "Use terms a 12-year-old can understand.",
    "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]
prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'audience'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}{' for' if row['audience'] else ''} {row['audience']}. {row['task part 2']}", 
    axis=1)
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step                                        task part 1  \
0                                Summarize for a LinkedIn post   
1                                Summarize for a LinkedIn post   
2            Describe the interesting points to your cowork...   
3            Describe the interesting points to your cowork...   

                                       task part 2      audience  \
0          Use terms a 12-year-old can understand.  lay audience   
1  Assume your audience has no science background.  lay audience   
2          Use terms a 12-year-old can understand.  lay audience   
3  Assume your audience has no science background.  lay audience   

                                              prompt  
0   Summarize for a LinkedIn post for lay audienc...  
1   Summarize for a LinkedIn post for lay audienc...  
2   Describe the interesting points to your cowor...  
3   Describe the interesting points to your cowor...

In [18]:
for index, prompt in prompts_df['prompt'].items():
    print(prompt)

 Summarize for a LinkedIn post for lay audience. Use terms a 12-year-old can understand.
 Summarize for a LinkedIn post for lay audience. Assume your audience has no science background.
 Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand.
 Describe the interesting points to your coworker at the water cooler for lay audience. Assume your audience has no science background.


## Run the experiment

In [22]:
iteration_id = 1
qna_dict=dict()
chatbot_dict=dict()
qna_dict, chatbot_dict = batch_summarize (text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id)

**Text #1 prompt #0 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #1 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #2 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #3 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #2 prompt #0 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #2 prompt #1 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #2 prompt #2 of 3**
Done creating prompt
Send

In [28]:
qna_dict[1]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [26]:
save_output(qna_dict[1], description='prompt_experiment')

File saved:  C:/Users/silvh/OneDrive/lighthouse/Ginkgo coding/content-summarization/output/pickles/prompt_experiment_2023-04-10_1336.sav
Time completed: 2023-04-10 13:36:22.505194
	Object saved as pickle
File saved:  C:/Users/silvh/OneDrive/lighthouse/Ginkgo coding/content-summarization/output/CSV/prompt_experiment_2023-04-10_1336.csv
Time completed: 2023-04-10 13:36:22.520199
	DataFrame saved as CSV


# Experiment 2

In [31]:
experiment_num = 2

prep_step = [
    # "Take the key points to",
    # "Take the key points and numerical descriptors to",
    ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    # "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    "lay audience",
    # ""
    # "seniors"
]
task_part2 = [
    # "",
    "Use terms a 12-year-old can understand.",
    "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    "Add 1-2 sentences to make this relevant for older adults."
]
prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}{' for' if row['audience'] else ''} {row['audience']}. {row['task part 2']} {row['task part 3']}", 
    axis=1)
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step  \
0             
1             

                                                            task part 1  \
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   

                                       task part 2  \
0          Use terms a 12-year-old can understand.   
1  Assume your audience has no science background.   

                                                 task part 3      audience  \
0  Add 1-2 sentences to make this relevant for older adults.  lay audience   
1  Add 1-2 sentences to make this relevant for older adults.  lay audience   

                                                                                                                                                                                              prompt  
0           Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Add 1-2 sentences to make this relevant for older adults.  
1   Describe the interesting points to your coworker at the water cooler for lay audience. Assume your audience has no science background. Add 1-2 sentences to make this relevant for older adults.

In [32]:
iteration_id = 2
qna_dict, chatbot_dict = batch_summarize (text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id)

**Text #1 prompt #0 of 1**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #1 of 1**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #2 prompt #0 of 1**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #2 prompt #1 of 1**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!


In [36]:
rating=dict()
rating[2] = pd.Series([5, 4, 3, 3])

In [33]:
qna_dict[2]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [68]:
qna_dict[2].columns = [i for i in range(qna_dict[2].shape[1])]
qna_dict[2]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [69]:
qna_dict[2].loc["Silvia's rating"] = rating[2]
qna_dict[2].tail()

0  \
task part 2                                                                                                                                                        Use terms a 12-year-old can understand.   
task part 3                                                                                                                                      Add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                      lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                          5   

                                                                                                                                                                                                                 1  \
task part 2                                                                                                                                                        Assume your audience has no science background.   
task part 3                                                                                                                                              Add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                              lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Assume your audience has no science background. Add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                                  4   

                                                                                                                                                                                                         2  \
task part 2                                                                                                                                                        Use terms a 12-year-old can understand.   
task part 3                                                                                                                                      Add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                      lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                          3   

                                                                                                                                                                                                                 3  
task part 2                                                                                                                                                        Assume your audience has no science background.  
task part 3     

# Experiment 3: text 2 only 

In [34]:
experiment_num = 3

prep_step = [
    # "Take the key points to",
    # "Take the key points and numerical descriptors to",
    ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    # "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    "lay audience",
    # ""
    # "seniors"
]
task_part2 = [
    # "",
    "Use terms a 12-year-old can understand.",
    "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    # "Add 1-2 sentences to make this relevant for older adults."
    "Once you are done, add 1-2 sentences to make this relevant for older adults."
]
prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}{' for' if row['audience'] else ''} {row['audience']}. {row['task part 2']} {row['task part 3']}", 
    axis=1)
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step  \
0             
1             

                                                            task part 1  \
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   

                                       task part 2  \
0          Use terms a 12-year-old can understand.   
1  Assume your audience has no science background.   

                                                                    task part 3  \
0  Once you are done, add 1-2 sentences to make this relevant for older adults.   
1  Once you are done, add 1-2 sentences to make this relevant for older adults.   

       audience  \
0  lay audience   
1  lay audience   

                                                                                                                                                                                                                 prompt  
0           Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Once you are done, add 1-2 sentences to make this relevant for older adults.  
1   Describe the interesting points to your coworker at the water cooler for lay audience. Assume your audience has no science background. Once you are done, add 1-2 sentences to make this relevant for older adults.

In [50]:
iteration_id = 3
qna_dict, chatbot_dict = batch_reply (text_dict[2], prompts_df, qna_dict,  chatbot_dict, iteration_id)

**Prompt #0 of 2**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
Error making chatbot request


In [51]:
qna_dict[3]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

## Iteration 1

In [53]:
iteration_id = 3.1
qna_dict, chatbot_dict = batch_reply2(text_dict[2], prompts_df, qna_dict,  chatbot_dict, iteration_id)

**Prompt #0 of 2**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
**Prompt #1 of 2**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3


In [55]:
rating[3.1] = [3, 5]

In [56]:
qna_dict[3.1].loc["Silvia's rating"] = rating[3.1]
qna_dict[3.1]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [70]:
qna_dict[3.1].tail()

0  \
task part 2                                                                                                                                                                           Use terms a 12-year-old can understand.   
task part 3                                                                                                                                      Once you are done, add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                                         lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Once you are done, add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                                             3   

                                                                                                                                                                                                                                    1  
task part 2                                                                                                                                                                           Assume your audience has no science background.  
task part 3                                                                                                                                              Once you are done, add 1-2 sentences to make this relevant for older adults.  
audience                                                                                                                                                                                                                 lay audience  
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Assume your audience has no science background. Once you are done, add 1-2 sentences to make this relevant for older adults.  
Silvia's rating                                                                                                                                                                                                                     5

In [71]:
pd.concat([qna_dict[2], qna_dict[3.1]], axis=1).tail()

0  \
task part 2                                                                                                                                                        Use terms a 12-year-old can understand.   
task part 3                                                                                                                                      Add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                      lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                          5   

                                                                                                                                                                                                                 1  \
task part 2                                                                                                                                                        Assume your audience has no science background.   
task part 3                                                                                                                                              Add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                              lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Assume your audience has no science background. Add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                                  4   

                                                                                                                                                                                                         2  \
task part 2                                                                                                                                                        Use terms a 12-year-old can understand.   
task part 3                                                                                                                                      Add 1-2 sentences to make this relevant for older adults.   
audience                                                                                                                                                                                      lay audience   
prompt            Describe the interesting points to your coworker at the water cooler for lay audience. Use terms a 12-year-old can understand. Add 1-2 sentences to make this relevant for older adults.   
Silvia's rating                                                                                                                                                                                          3   

                                                                                                                                                                                                                 3  \
task part 2                                                                                                                                                        Assume your audience has no science background.   
task part 3   

In [72]:
description = 'prompt_experiment'
save_output(pd.concat([qna_dict[2], qna_dict[3.1]], axis=1), description=description)

File saved:  C:/Users/silvh/OneDrive/lighthouse/Ginkgo coding/content-summarization/output/pickles/prompt_experiment_2023-04-10_1549.sav
Time completed: 2023-04-10 15:49:53.944876
	Object saved as pickle
File saved:  C:/Users/silvh/OneDrive/lighthouse/Ginkgo coding/content-summarization/output/CSV/prompt_experiment_2023-04-10_1549.csv
Time completed: 2023-04-10 15:49:53.970876
	DataFrame saved as CSV


# Experiment 4: Use prompt chains

## prepare test text

In [135]:
test_text = """Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
 = 0.37) and increased ratings of pain intensity (by 0.7 ± 0.7 cm; P = 0.004; η2p
 = 0.55) and unpleasantness (by 0.7 ± 0.9 cm; P = 0.02; η2p
 = 0.40); these results were not influenced by menstrual phase. Water ingestion reduced thirst perception (visual analog scale, by 2.3 ± 0.9 cm; P < 0.001, η2p
 = 0.88) but did not reduce pain sensitivity. Therefore, hypohydration increases pain sensitivity in women with no influence of menstrual phase.
"""

In [101]:
test_text

'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity i

## Prepare prompt chain

In [95]:
experiment_num = 4

prep_step = [
    # "Take the key points to",
    # "Take the key points and numerical descriptors to",
    ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    # "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    # "lay audience",
    "",
    "seniors",
    "people who enjoy sports"
]
task_part2 = [
    "",
    "Use terms a 12-year-old can understand.",
    # "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    "Add 1-2 sentences to make this relevant for"
    # "Add 1-2 sentences to make this relevant for older adults."
    # "Once you are done, add 1-2 sentences to make this relevant for older adults.",
    ""
]

prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}.", 
    axis=1)
prompts_df['simplify'] = prompts_df.apply(
    lambda row: f" {row['task part 2'] if row['task part 2'] else None}", 
    axis=1)
prompts_df['relevance'] = prompts_df.apply(
    lambda row: f" {row['task part 3']} {row['audience']} " if row['audience'] else None, 
    axis=1) 
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step                    task part 1  \
0            Summarize for a LinkedIn post   
1            Summarize for a LinkedIn post   
2            Summarize for a LinkedIn post   
3            Summarize for a LinkedIn post   
4            Summarize for a LinkedIn post   
5            Summarize for a LinkedIn post   

                               task part 2  \
0                                            
1                                            
2                                            
3  Use terms a 12-year-old can understand.   
4  Use terms a 12-year-old can understand.   
5  Use terms a 12-year-old can understand.   

                                   task part 3                 audience  \
0  Add 1-2 sentences to make this relevant for                            
1  Add 1-2 sentences to make this relevant for                  seniors   
2  Add 1-2 sentences to make this relevant for  people who enjoy sports   
3  Add 1-2 sentences to make this relevant for                            
4  Add 1-2 sentences to make this relevant for                  seniors   
5  Add 1-2 sentences to make this relevant for  people who enjoy sports   

                            prompt                                  simplify  \
0   Summarize for a LinkedIn post.                                      None   
1   Summarize for a LinkedIn post.                                      None   
2   Summarize for a LinkedIn post.                                      None   
3   Summarize for a LinkedIn post.   Use terms a 12-year-old can understand.   
4   Summarize for a LinkedIn post.   Use terms a 12-year-old can understand.   
5   Summarize for a LinkedIn post.   Use terms a 12-year-old can understand.   

                                                               relevance  
0                                                                   None  
1                   Add 1-2 sentences to make this relevant for seniors   
2   Add 1-2 sentences to make this relevant for people who enjoy sports   
3                                                                   None  
4                   Add 1-2 sentences to make this relevant for seniors   
5   Add 1-2 sentences to make this relevant for people who enjoy sports

In [ ]:
# def reply_chain(task, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
#           text_key=['text_discussion'],
#         system_role = "You are an expert at science communication."
#         ):
#     """
#     Send a ChatCompletion request to ChatGPT via the Chatbot class.

#     Requrired paramaters:
#         - task (str): Task to include in ChatGPT prompt.
#         - text (str): Text to feed to GPT for summarization.

#     Optional parameters
#         - system_role (str): ChatGPT parameter. 
#             Default is "You are an expert at science communication."
#         - temperature (float): ChatGPT parameter. Default is 0.7.
#         - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
#         - max_tokens (int): Token limit for ChatGPT response.
#         - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
#     """
#     chatbot = Chatbot(text,
#         system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
#         max_tokens=max_tokens
#         )
#     prompt = chatbot.create_prompt(task)
#     firstline_pattern = r'\s?(\S*)(\n*)(.+)'
#     title = re.match(firstline_pattern, text)[0]
#     qna = dict()
#     qna['article_title'] = title
#     qna['system_role'] = system_role
#     qna['prompt'] = task
#     qna['model'] = model
#     try:
#         response = chatbot.gpt(prompt)
#     except:
#         print('\t**API request failed**')
#         return qna, chatbot

#     simplify_bot = Chatbot(text,
#         system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
#         max_tokens=max_tokens
#         )
#     simplify_prompt = simplify_bot.create_prompt(task)





#     try:
#         for index, choice in enumerate(response.choices):
#             qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
#         qna[f'text'] = text
#         return qna, chatbot
#     except:
#         print('\t**Error with response parsing**')
#         return qna, response

# def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, prompt_column='prompt',
#     save_outputs=False, filename=None, append_version=False,
#     csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
#     pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
#     ):
#     """
#     Summarize multiple texts using the same prompts.
#     Parameters:
#         - prompts_df: DataFrame containing the prompts.
#         - qna_dict: Dictionary to store the input and outputs.
#         - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
#         - prompt_column (str): Name of the column in the prompts_df containing the user input.

#     """
#     temp_qna_dict = dict()
#     prompts_df = prompts_df.reset_index(drop=True)
#     qna_dfs_list = []
#     for key in text_dict:
#         text = text_dict[key]
#         temp_qna_dict[key] = dict()
#         for index, input in prompts_df['prompt'].items():
#             print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
#             try:
#                 temp_qna_dict[key][index], chatbot_dict[f'{iteration_id}_text{key}_prompt{index}'] = reply(input, text)
#                 print('\t...Success!')
#             except:
#                 print('\t...Error making chatbot request')
#                 break
#         try:
#             updated_qna_dict = pd.concat([
#                 pd.DataFrame(temp_qna_dict[key]),
#                 prompts_df.transpose()
#             ])
#         except:
#             print('Error concatenating prompts DataFrame')
#             return temp_qna_dict, chatbot_dict
#         try:
#             qna_dfs_list.append(updated_qna_dict)
#             qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
#             if save_outputs:
#                 try:
#                     append_version = append_version if filename else False
#                     filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
#                     savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
#                     save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
#                 except:
#                     print('Unable to save outputs')
#         except:
#             print('Error concatenating DataFrames')
#     return qna_dict, chatbot_dict

## Iteration 1

In [108]:
class Chaining:

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def summarize(task, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summary = dict()
        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summary[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

iteration_id = 1
qna_dict = dict()
chatbot_dict = dict()
chaining_dict = dict()
chain = Chaining()
chaining_dict[iteration_id] = chain
qna_dict[iteration_id], chatbot_dict[iteration_id] = chain.summarize(test_text)


Done creating prompt


NameError: name 'self' is not defined

## Iteration 2

In [109]:
class Chaining:

    def __init__(self):
        self.summary = None

    def summarize(self, task, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summary = dict()
        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summary[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

iteration_id = 1
qna_dict = dict()
chatbot_dict = dict()
chaining_dict = dict()
chain = Chaining()
chaining_dict[iteration_id] = chain

qna_dict[iteration_id], chatbot_dict[iteration_id] = chain.summarize(prompts_df.loc[0,'prompt'], test_text)

Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3


In [110]:
qna_dict[iteration_id]

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [113]:
chain.summary

{'response_01': 'Chronic pain is a major health issue that comes with high costs. Unfortunately, current pain treatments often fall short due to the complex nature of pain. Recent research has shown that mild dehydration can increase pain sensitivity in men, and this study aimed to see if the same was true for women during different phases of their menstrual cycle. The study found that hypohydration did increase pain sensitivity in women but was not influenced by menstrual phase. While drinking water did reduce thirst, it did not relieve pain sensitivity. These findings shed light on the importance of adequate hydration for pain management. #ChronicPain #Hydration #WomenHealth #MenstrualCycle',
 'response_02': 'Chronic pain is a major health issue with significant socioeconomic costs. However, current pain treatments are often ineffective due to the complexity of pain. Mild dehydration has been shown to increase pain sensitivity in men, but whether this holds true for women remains unc

In [114]:
chaining_dict[iteration_id].summary

{'response_01': 'Chronic pain is a major health issue that comes with high costs. Unfortunately, current pain treatments often fall short due to the complex nature of pain. Recent research has shown that mild dehydration can increase pain sensitivity in men, and this study aimed to see if the same was true for women during different phases of their menstrual cycle. The study found that hypohydration did increase pain sensitivity in women but was not influenced by menstrual phase. While drinking water did reduce thirst, it did not relieve pain sensitivity. These findings shed light on the importance of adequate hydration for pain management. #ChronicPain #Hydration #WomenHealth #MenstrualCycle',
 'response_02': 'Chronic pain is a major health issue with significant socioeconomic costs. However, current pain treatments are often ineffective due to the complexity of pain. Mild dehydration has been shown to increase pain sensitivity in men, but whether this holds true for women remains unc

In [115]:
iteration_id

1

## Iteration 2.2: Simplify

In [117]:
prompts_df.loc[5,'simplify']

' Use terms a 12-year-old can understand.'

In [124]:
class Chaining:

    def __init__(self):
        self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def summarize(self, task, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summary = dict()
        self.article_title = qna['article_title']
        self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summary[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        try:
            for key in self.summary:
                self.simplify_bot_dict[key] = Chatbot(
                    summary[key], system_role=system_role,
                    model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                    )
                simplify_prompt = self.simplify_bot_dict[key].create_prompt(simplify_task)
                try:
                    self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt).choices[0]["message"]["content"]
                except:
                    self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt)
            return self.simple_summary_dict
        except:
            print('\t**Error with simplifying summaries**')
            return self.simple_summary_dict

        

iteration_id = 2.2

chaining_dict[iteration_id] = Chaining()

qna_dict[iteration_id], chatbot_dict[iteration_id] = chain.summarize(prompts_df.loc[0,'prompt'], test_text)
simple_summary_dict = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	**Error with simplifying summaries**


In [125]:
chaining_dict[iteration_id].summary

In [127]:
print('Iteration_id:', iteration_id)
qna_dict[iteration_id]

Iteration_id: 2.2


{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

## Iteration 3

In [128]:
class Chaining:

    def __init__(self):
        self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def summarize(self, task, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summary = dict()
        self.article_title = qna['article_title']
        self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summary[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key in self.summary:
            self.simplify_bot_dict[key] = Chatbot(
                summary[key], system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt)
        return self.simple_summary_dict
        # except:
        #     print('\t**Error with simplifying summaries**')
            # return self.simple_summary_dict

        

iteration_id = 3

chaining_dict[iteration_id] = Chaining()

qna_dict[iteration_id], chatbot_dict[iteration_id] = chain.summarize(prompts_df.loc[0,'prompt'], test_text)
simple_summary_dict = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3


TypeError: 'NoneType' object is not iterable

In [129]:
chaining_dict[iteration_id].text

AttributeError: 'Chaining' object has no attribute 'text'

### 3.1

In [133]:
class Chaining:

    # def __init__(self):
    #     self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = qna['article_title']
        # self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = self.text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key in self.summary:
            self.simplify_bot_dict[key] = Chatbot(
                summary[key], system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt)
        return self.simple_summary_dict
        # except:
        #     print('\t**Error with simplifying summaries**')
            # return self.simple_summary_dict

        

iteration_id = 3.1
simple_summary_dict = dict()

chaining_dict[iteration_id] = Chaining(test_text)

qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'])
simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3


AttributeError: 'Chaining' object has no attribute 'summary'

In [134]:
chaining_dict[iteration_id].text

'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity i

In [136]:
class Chaining:

    # def __init__(self):
    #     self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = qna['article_title']
        # self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = self.text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key in self.summaries_dict:
            self.simplify_bot_dict[key] = Chatbot(
                summaries_dict[key], system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt)
        return self.simple_summary_dict
        # except:
        #     print('\t**Error with simplifying summaries**')
            # return self.simple_summary_dict

        

iteration_id = 3.1
n_choices=2
simple_summary_dict = dict()


chaining_dict[iteration_id] = Chaining(test_text)

qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 2 choices using gpt-3.5-turbo
	**API request failed**


In [138]:
qna_dict[3.1]

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [137]:
iteration_id = 3.12
n_choices=2
simple_summary_dict = dict()


chaining_dict[iteration_id] = Chaining(test_text)

qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 2 choices using gpt-3.5-turbo
Done sending request to GPT-3


NameError: name 'summaries_dict' is not defined

### 3.2: `simplify` method successful

In [140]:
class Chaining:

    # def __init__(self):
    #     self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = qna['article_title']
        # self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = self.text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            self.simplify_bot_dict[key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[key] = self.simplify_bot_dict[key].gpt(simplify_prompt)
        return self.simple_summary_dict
        # except:
        #     print('\t**Error with simplifying summaries**')
            # return self.simple_summary_dict

        

iteration_id = 3.2
n_choices=2
simple_summary_dict = dict()


chaining_dict[iteration_id] = Chaining(test_text)

qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 2 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3


In [146]:
prompts_df.loc[0,'prompt']

' Summarize for a LinkedIn post.'

In [145]:
prompts_df.loc[5,'simplify']

' Use terms a 12-year-old can understand.'

In [141]:
qna_dict[iteration_id]

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [142]:
simple_summary_dict[iteration_id]

{'response_01': "Chronic pain is when someone has pain that lasts a long time and it can be really expensive to treat. Scientists did a study to see if not drinking enough water could make pain worse for women during different times of the month. They found that not drinking enough water made the pain worse, but drinking more water didn't make it better. This means that drinking enough water might help women manage their pain better.",
 'response_02': "Chronic pain is when someone has pain that lasts for a long time and it can be really hard to treat. A new study found that not drinking enough water can make the pain worse for women, even if they are not on their period. Drinking water after becoming dehydrated doesn't make the pain go away either. This study shows that it's important to drink enough water to help manage chronic pain."}

In [144]:
chaining_dict[iteration_id].summaries_dict

{'response_01': "Chronic pain is a major health issue with high costs, but current treatments often fall short. A recent study investigated the effects of mild dehydration on pain sensitivity in women during different menstrual phases. Results showed that dehydration increased pain sensitivity, but water ingestion did not reduce it. These findings suggest that hydration may play a role in pain management for women. #ChronicPain #Women'sHealth #Hydration",
 'response_02': '"Chronic pain is a significant health issue that affects many people, and current treatments are often ineffective due to the complex nature of pain. A recent study found that mild dehydration can increase pain sensitivity in women, regardless of menstrual phase. The study also showed that drinking water does not reverse the negative effects of dehydration on pain sensitivity. This research sheds light on the importance of proper hydration in managing chronic pain."'}

In [148]:
[re.sub(r'response', r'simple_summary', key) for key in qna_dict[iteration_id].keys()]


['article_title',
 'system_role',
 'prompt',
 'model',
 'simple_summary_01',
 'simple_summary_02',
 'text']

## Iteration 4

In [150]:
class Chaining:

    # def __init__(self):
    #     self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        qna = dict()
        qna['article_title'] = title
        qna['system_role'] = system_role
        qna['prompt'] = task
        qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = qna['article_title']
        # self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            qna[f'text'] = self.text
            return qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', r'simple_summary', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        return self.simple_summary_dict
        # except:
        #     print('\t**Error with simplifying summaries**')
            # return self.simple_summary_dict

        

iteration_id = 4
n_choices=2
simple_summary_dict = dict()


chaining_dict[iteration_id] = Chaining(test_text)

qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 2 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3


In [151]:
chaining_dict[iteration_id].summaries_dict

{'response_01': 'Chronic pain is a major health problem with significant socioeconomic costs, but current treatments are often ineffective due to the complex nature of pain. A new study found that mild dehydration can increase pain sensitivity in women, regardless of menstrual phase. Drinking water did not reduce pain sensitivity but did reduce thirst perception. These findings highlight the importance of proper hydration for pain management in women. #chronicpain #hydration #womenshealth #painmanagement',
 'response_02': 'Chronic pain is a major health issue with significant socioeconomic costs. However, current pain treatments are often ineffective due to the multifactorial nature of pain. A recent study investigated the effects of mild hypohydration on pain sensitivity in women during different menstrual phases. The results showed that hypohydration increased pain sensitivity in women with no influence of menstrual phase. The study highlights the importance of maintaining proper hyd

In [152]:
chaining_dict[iteration_id].simple_summary_dict

{'simple_summary_01': "Chronic pain is when someone has pain that lasts a long time and it can be a big problem for their health and money. Sometimes, the treatments for pain don't work well because pain is complicated. A new study found that not drinking enough water can make pain worse for women, even if they are not on their period. Drinking water didn't make the pain go away, but it did make people less thirsty. This study shows that it's important for women to drink enough water to help manage their pain.",
 'simple_summary_02': "Chronic pain is when someone has pain that lasts a long time and it can be a big problem for their health and money. But, the treatments we have now don't always work because pain is caused by many things. A new study looked at how not drinking enough water affects how much pain women feel during different times of the month. The study found that not drinking enough water makes women feel more pain, no matter what time of the month it is. This study shows

In [154]:
{**qna_dict[iteration_id], **chaining_dict[iteration_id].simple_summary_dict}

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [160]:
my_dict = {**qna_dict[iteration_id], **chaining_dict[iteration_id].simple_summary_dict}

In [161]:
my_dict.update({'text': my_dict.pop('text')})

In [162]:
my_dict

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

### 4.1

In [164]:
class Chaining:

    # def __init__(self):
    #     self.summary = None

    # def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
    #       text_key=['text_discussion']
    #     )
    #     self.text = text
    #     self.model = model
    #     self.temperature = temperature
    #     self.n_choices = n_choices
    #     self.max_tokens = max_tokens

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title
        # self.text = text

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna, chatbot
        except:
            print('\t**Error with response parsing**')
            return self.qna, response

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', r'simple_summary', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.qna

        

iteration_id = 4.1
n_choices=2
simple_summary_dict = dict()


chaining_dict[iteration_id] = Chaining(test_text)

qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 2 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3


In [165]:
chaining_dict[iteration_id].qna

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [166]:
simple_summary_dict[iteration_id]

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

# Update prompts_df

In [10]:
from itertools import product
prompts_dict = dict()
experiment_num = 5

prep_step = [
    # "Take the key points to",
    "Take the key points and numerical descriptors to",
    # ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    # "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    # "lay audience",
    "",
    "seniors",
    # "people who enjoy sports"
]
task_part2 = [
    "",
    "Use terms a 12-year-old can understand.",
    # "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    "Add 1-2 sentences to make this relevant for"
    # "Add 1-2 sentences to make this relevant for older adults."
    # "Once you are done, add 1-2 sentences to make this relevant for older adults.",
    ""
]

prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}.", 
    axis=1)
prompts_df['simplify'] = prompts_df.apply(
    lambda row: f" {row['task part 2'] if row['task part 2'] else ''}", 
    axis=1)
prompts_df['relevance'] = prompts_df.apply(
    lambda row: f" {row['task part 3']} {row['audience']} " if row['audience'] else '', 
    axis=1) 
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
3  Take the key points and numerical descriptors to   

                     task part 1                              task part 2  \
0  Summarize for a LinkedIn post                                            
1  Summarize for a LinkedIn post                                            
2  Summarize for a LinkedIn post  Use terms a 12-year-old can understand.   
3  Summarize for a LinkedIn post  Use terms a 12-year-old can understand.   

                                   task part 3 audience  \
0  Add 1-2 sentences to make this relevant for            
1  Add 1-2 sentences to make this relevant for  seniors   
2  Add 1-2 sentences to make this relevant for            
3  Add 1-2 sentences to make this relevant for  seniors   

                                              prompt  \
0  Take the key points and numerical descriptors ...   
1  Take the key points and numerical descriptors ...   
2  Take the key points and numerical descriptors ...   
3  Take the key points and numerical descriptors ...   

                                   simplify  \
0                                             
1                                             
2   Use terms a 12-year-old can understand.   
3   Use terms a 12-year-old can understand.   

                                           relevance  
0                                                     
1   Add 1-2 sentences to make this relevant for s...  
2                                                     
3   Add 1-2 sentences to make this relevant for s...

# Iteration 5

In [172]:
test_text_dict = create_text_dict(test_text)
test_text_dict.keys()

dict_keys([1])

In [178]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', r'simple_summary', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.qna

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df['prompt'].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, text)
                chatbot_dict[iteration_id][f'text{key}_prompt{index}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

iteration_id = 5
n_choices=2

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, iteration_id=iteration_id)


# chaining_dict[iteration_id] = Chaining(test_text)

# qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
# simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

**Text #1 prompt #0 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negativ

In [182]:
chaining_dict[5]['text1_prompt0'].text

'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity i

In [179]:
qna_dict[5]

0  \
0            {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p', 'system_role': 'You are an expert at science communication.', 'prompt': 'Take the key points and numerical descriptors to Summarize for a LinkedIn post.', 'model': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
 = 0.37) and increased ratings of pain intensity (by 0.7 ± 0.7 cm; P = 0.004; η2p
 = 0.55) and unpleasantness (by 0.7 ± 0.9 cm; P = 0.02; η2p
 = 0.40); these results were not influenced by menstrual phase. Water ingestion reduced thirst perception (visual analog scale, by 2.3 ± 0.9 cm; P < 0.001, η2p
 = 0.88) but did not reduce pain sensitivity. Therefore, hypohydration increases pain sensitivity in women with no influence of menstrual phase.
'}   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

# Update test_text

In [134]:
test_text2 = """Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p

 = 0.37) and increased ratings of pain intensity (by 0.7 ± 0.7 cm; P = 0.004; η2p
 = 0.55) and unpleasantness (by 0.7 ± 0.9 cm; P = 0.02; η2p
 = 0.40); these results were not influenced by menstrual phase. Water ingestion reduced thirst perception (visual analog scale, by 2.3 ± 0.9 cm; P < 0.001, η2p
 = 0.88) but did not reduce pain sensitivity. Therefore, hypohydration increases pain sensitivity in women with no influence of menstrual phase.
"""

In [7]:
test_text_dict = create_text_dict(test_text2)
test_text_dict.keys()

dict_keys([1])

## Iteration 5.2

In [185]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', r'simple_summary', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.qna

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df['prompt'].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

iteration_id = 5.2
n_choices=2

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, iteration_id=iteration_id)


# chaining_dict[iteration_id] = Chaining(test_text)

# qna_dict[iteration_id], chatbot_dict[iteration_id] = chaining_dict[iteration_id].summarize(prompts_df.loc[0,'prompt'], n_choices=n_choices)
# simple_summary_dict[iteration_id] = chaining_dict[iteration_id].simplify(prompts_df.loc[5,'simplify'])

**Text #1 prompt #0 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #1 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #2 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!
**Text #1 prompt #3 of 3**
Done creating prompt
Sending request to GPT-3
	Requesting 5 choices using gpt-3.5-turbo
Done sending request to GPT-3
	...Success!


In [186]:
qna_dict[5.2]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p   
system_role                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       You are an expert at science communication.   
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [187]:
chaining_dict[5.2].keys()

dict_keys(['text1_prompt00', 'text1_prompt01', 'text1_prompt02', 'text1_prompt03'])

In [192]:
chaining_dict[5.2]['text1_prompt00'].simplify(prompts_df.loc[3,'simplify'])

Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3


{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [210]:
simplify_prompts = [
    "",
    "Use terms a 12-year-old can understand.",
    "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

In [214]:
def simplify_chaining_dict(chaining_dict, simplify_prompts):
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1 ]
    for key in chaining_dict:
        print(chaining_dict[key].qna['prompt'])
        for prompt in simplify_prompts:
            print(prompt)
        

simplify_chaining_dict(chaining_dict[5.2], simplify_prompts)

Take the key points and numerical descriptors to Summarize for a LinkedIn post.
Use terms a 12-year-old can understand.
Assume your audience has no science background.
Take the key points and numerical descriptors to Summarize for a LinkedIn post.
Use terms a 12-year-old can understand.
Assume your audience has no science background.
Take the key points and numerical descriptors to Summarize for a LinkedIn post.
Use terms a 12-year-old can understand.
Assume your audience has no science background.
Take the key points and numerical descriptors to Summarize for a LinkedIn post.
Use terms a 12-year-old can understand.
Assume your audience has no science background.


In [218]:
def simplify_chaining_dict(chaining_dict, simplify_prompts):
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1 ]
    for text_prompt_key in chaining_dict:
        print(text_prompt_key)

        for key in chaining_dict[text_prompt_key].qna:
            print(f'\t{key}')
        # for prompt in simplify_prompts:
        #     print(prompt)
        

simplify_chaining_dict(chaining_dict[5.2], simplify_prompts)

text1_prompt00
	article_title
	system_role
	prompt
	model
	response_01
	response_02
	response_03
	response_04
	response_05
	simple_summary_01
	simple_summary_02
	simple_summary_03
	simple_summary_04
	simple_summary_05
	text
text1_prompt01
	article_title
	system_role
	prompt
	model
	response_01
	response_02
	response_03
	response_04
	response_05
	text
text1_prompt02
	article_title
	system_role
	prompt
	model
	response_01
	response_02
	response_03
	response_04
	response_05
	text
text1_prompt03
	article_title
	system_role
	prompt
	model
	response_01
	response_02
	response_03
	response_04
	response_05
	text


In [223]:
def simplify_chaining_dict(chaining_dict, simplify_prompts):
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1 ]
    for text_prompt in chaining_dict:
        print(text_prompt)
        summary_keys = [key for key in chaining_dict[text_prompt].qna if 'response' in key]

        for summary_key in summary_keys:
            summary = chaining_dict[text_prompt].qna[summary_key]
            print(summary)
        # for prompt in simplify_prompts:
        #     print(prompt)
        

simplify_chaining_dict(chaining_dict[5.2], simplify_prompts)

text1_prompt00
Chronic pain is a major problem with high socioeconomic costs. Current treatments are often ineffective due to the multifactorial nature of pain. Mild hypohydration has been shown to increase experimental pain sensitivity in men, and now, a study has found that it also increases pain sensitivity in women. The study investigated the effects of mild hypohydration on ischemic pain sensitivity in 14 eumenorrheic women and found that it reduced pain tolerance by 34±46 seconds, increased ratings of pain intensity by 0.7±0.7 cm, and unpleasantness by 0.7±0.9 cm. These results were not influenced by menstrual phase. Water ingestion did not reduce pain sensitivity, but it did reduce thirst perception.
Chronic pain is a major health issue with high costs, but current treatments are often ineffective. Mild hypohydration can increase pain sensitivity in men, and this study shows it can also happen in women. It affects pain tolerance, intensity, and unpleasantness. Menstrual phase do

In [230]:
prompts_df

prep_step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
3  Take the key points and numerical descriptors to   

                     task part 1                              task part 2  \
0  Summarize for a LinkedIn post                                            
1  Summarize for a LinkedIn post                                            
2  Summarize for a LinkedIn post  Use terms a 12-year-old can understand.   
3  Summarize for a LinkedIn post  Use terms a 12-year-old can understand.   

                                   task part 3 audience  \
0  Add 1-2 sentences to make this relevant for            
1  Add 1-2 sentences to make this relevant for  seniors   
2  Add 1-2 sentences to make this relevant for            
3  Add 1-2 sentences to make this relevant for  seniors   

                                                                            prompt  \
0  Take the key points and numerical descriptors to Summarize for a LinkedIn post.   
1  Take the key points and numerical descriptors to Summarize for a LinkedIn post.   
2  Take the key points and numerical descriptors to Summarize for a LinkedIn post.   
3  Take the key points and numerical descriptors to Summarize for a LinkedIn post.   

                                   simplify  \
0                                      None   
1                                      None   
2   Use terms a 12-year-old can understand.   
3   Use terms a 12-year-old can understand.   

                                               relevance  
0                                                   None  
1   Add 1-2 sentences to make this relevant for seniors   
2                                                   None  
3   Add 1-2 sentences to make this relevant for seniors

# Iteration 6

In [ ]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.qna

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df['prompt'].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_dict, iteration_id,
    prompt_column='simplify'):
    qna_chain_dict[iteration_id] = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_dict:
        print(f'{text_prompt_key}')
        summary_keys = [key for key in chaining_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            summary = chaining_dict[text_prompt_key].qna[summary_key]
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                qna_chain_dict[iteration_id][summary_key] = dict()
                qna_chain_dict[iteration_id][summary_key][index] = chaining_dict[text_prompt_key].simplify(
                    prompt, 
                    # simplify_iteration=index
                    )
    return qna_chain_dict



iteration_id = 6
qna_chain_dict = dict()
qna_chain_dict = simplify_chaining_dict(prompts_df, qna_chain_dict, chaining_dict[5.2], iteration_id,
    # simplify_iteration=1
    )

text1_prompt00
	Simplifying response_01...
	...Prompt:  Use terms a 12-year-old can understand.
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
	Simplifying response_02...
	...Prompt:  Use terms a 12-year-old can understand.
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT-3
Done creating prompt
Sending request to GPT-3
	Requesting 1 choices using gpt-3.5-turbo
Done sending request to GPT

## 6.2 [After restarting VS Code]

In [12]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.qna

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in enumerate(prompts_df['prompt'].unique()):
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_dict, iteration_id,
    prompt_column='simplify'):
    qna_chain_dict[iteration_id] = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_dict:
        print(f'{text_prompt_key}')
        summary_keys = [key for key in chaining_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            summary = chaining_dict[text_prompt_key].qna[summary_key]
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                # qna_chain_dict[iteration_id][summary_key] = dict()
                # qna_chain_dict[iteration_id][summary_key][index] = chaining_dict[text_prompt_key].simplify(
                #     prompt, 
                #     simplify_iteration=index
                #     )
    return qna_chain_dict



iteration_id = 6.2
n_choices = 2
qna_dict = dict()
qna_chain_dict = dict()
chatbot_dict = dict()
qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)

# qna_chain_dict = simplify_chaining_dict(prompts_df, qna_chain_dict, chaining_dict[5.2], iteration_id,
#     simplify_iteration=1
#     )

**Text #1 prompt #0 of 3**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
**Text #1 prompt #1 of 3**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
**Text #1 prompt #2 of 3**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
**Text #1 prompt #3 of 3**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!


In [13]:
qna_dict[6.2]

0  \
article_title  Chronic pain is a pervasive health problem and...   
system_role          You are an expert at science communication.   
prompt         Take the key points and numerical descriptors ...   
model                                              gpt-3.5-turbo   
response_01    Chronic pain affects many people and is costly...   
response_02    Chronic pain is a major health issue with high...   
text           Chronic pain is a pervasive health problem and...   
prep_step       Take the key points and numerical descriptors to   
task part 1                        Summarize for a LinkedIn post   
task part 2                                                        
task part 3          Add 1-2 sentences to make this relevant for   
audience                                                           
prompt         Take the key points and numerical descriptors ...   
simplify                                                           
relevance                                                          

                                                               1  \
article_title  Chronic pain is a pervasive health problem and...   
system_role          You are an expert at science communication.   
prompt         Take the key points and numerical descriptors ...   
model                                              gpt-3.5-turbo   
response_01    "Chronic pain is a major health issue with hig...   
response_02    "Chronic pain is a significant health issue wi...   
text           Chronic pain is a pervasive health problem and...   
prep_step       Take the key points and numerical descriptors to   
task part 1                        Summarize for a LinkedIn post   
task part 2                                                        
task part 3          Add 1-2 sentences to make this relevant for   
audience                                                 seniors   
prompt         Take the key points and numerical descriptors ...   
simplify                                                           
relevance       Add 1-2 sentences to make this relevant for s...   

                                                               2  \
article_title  Chronic pain is a pervasive health problem and...   
system_role          You are an expert at science communication.   
prompt         Take the key points and numerical descriptors ...   
model                                              gpt-3.5-turbo   
response_01    Chronic pain is a major health issue with sign...   
response_02    Chronic pain is a major health problem with hi...   
text           Chronic pain is a pervasive health problem and...   
prep_step       Take the key points and numerical descriptors to   
task part 1                        Summarize for a LinkedIn post   
task part 2              Use terms a 12-year-old can understand.   
task part 3          Add 1-2 sentences to make this relevant for   
audience                                                           
prompt         Take the key points and numerical descriptors ...   
simplify                 Use terms a 12-year-old can understand.   
relevance                                                          

                                                               3  
article_title  Chronic pain is a pervasive health problem and...  
system_role          You are an expert at science communication.  
prompt         Take the key points and numerical descriptors ...  
model                                              gpt-3.5-turbo  
response_01    "Chronic pain is a major health issue with hig...  
response_02    "Chronic pain is a major issue with high socio...  
text           Chronic pain is a pervasive health problem and...  
prep_step       Take the key points and numerical descriptors to  
task part 1                        Summarize for a LinkedIn post  
task part 2              Use terms a 12-year-old can understand.  
task part 3          Add 1-2 sentences to make this relevan

In [16]:
chaining_dict[6.2].keys()

dict_keys(['text1_prompt00', 'text1_prompt01', 'text1_prompt02', 'text1_prompt03'])

In [24]:
qna_chain_dict = simplify_chaining_dict(prompts_df, qna_chain_dict, chaining_dict[6.2], iteration_id,
    # simplify_iteration=1
    )
qna_chain_dict[6.2]

text1_prompt00
	Simplifying response_01...
	...Prompt:  Use terms a 12-year-old can understand.
	Simplifying response_02...
	...Prompt:  Use terms a 12-year-old can understand.
text1_prompt01
	Simplifying response_01...
	...Prompt:  Use terms a 12-year-old can understand.
	Simplifying response_02...
	...Prompt:  Use terms a 12-year-old can understand.
text1_prompt02
	Simplifying response_01...
	...Prompt:  Use terms a 12-year-old can understand.
	Simplifying response_02...
	...Prompt:  Use terms a 12-year-old can understand.
text1_prompt03
	Simplifying response_01...
	...Prompt:  Use terms a 12-year-old can understand.
	Simplifying response_02...
	...Prompt:  Use terms a 12-year-old can understand.


{}

# Shorten prompts_df

In [26]:
# from itertools import product
# prompts_dict = dict()
experiment_num = 6

prep_step = [
    # "Take the key points to",
    "Take the key points and numerical descriptors to",
    # ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    # "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    # "lay audience",
    # "",
    "seniors",
    # "people who enjoy sports"
]
task_part2 = [
    "",
    "Use terms a 12-year-old can understand.",
    # "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    "Add 1-2 sentences to make this relevant for"
    # "Add 1-2 sentences to make this relevant for older adults."
    # "Once you are done, add 1-2 sentences to make this relevant for older adults.",
    ""
]

prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}.", 
    axis=1)
prompts_df['simplify'] = prompts_df.apply(
    lambda row: f" {row['task part 2'] if row['task part 2'] else ''}", 
    axis=1)
prompts_df['relevance'] = prompts_df.apply(
    lambda row: f" {row['task part 3']} {row['audience']} " if row['audience'] else '', 
    axis=1) 
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                     task part 1                              task part 2  \
0  Summarize for a LinkedIn post                                            
1  Summarize for a LinkedIn post  Use terms a 12-year-old can understand.   

                                   task part 3 audience  \
0  Add 1-2 sentences to make this relevant for  seniors   
1  Add 1-2 sentences to make this relevant for  seniors   

                                              prompt  \
0  Take the key points and numerical descriptors ...   
1  Take the key points and numerical descriptors ...   

                                   simplify  \
0                                             
1   Use terms a 12-year-old can understand.   

                                           relevance  
0   Add 1-2 sentences to make this relevant for s...  
1   Add 1-2 sentences to make this relevant for s...

# Iteration 7

In [27]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.qna

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in enumerate(prompts_df['prompt'].unique()):
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_dict, iteration_id,
    prompt_column='simplify', simplify_iteration=None):
    qna_chain_dict[iteration_id] = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_dict:
        print(f'{text_prompt_key}')
        summary_keys = [key for key in chaining_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            summary = chaining_dict[text_prompt_key].qna[summary_key]
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                qna_chain_dict[iteration_id][summary_key] = dict()
                qna_chain_dict[iteration_id][summary_key][index] = chaining_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
    return qna_chain_dict



iteration_id = 7
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()
qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)

# qna_chain_dict = simplify_chaining_dict(prompts_df, qna_chain_dict, chaining_dict[5.2], iteration_id,
#     simplify_iteration=1
#     )

**Text #1 prompt #0 of 1**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!


In [29]:
qna_dict[7]

0  \
article_title  Chronic pain is a pervasive health problem and...   
model                                              gpt-3.5-turbo   
prompt         Take the key points and numerical descriptors ...   
response_01    "Chronic pain is a major health issue with hig...   
response_02    "New study finds that mild hypohydration incre...   
system_role          You are an expert at science communication.   
text           Chronic pain is a pervasive health problem and...   
prep_step       Take the key points and numerical descriptors to   
task part 1                        Summarize for a LinkedIn post   
task part 2                                                        
task part 3          Add 1-2 sentences to make this relevant for   
audience                                                 seniors   
prompt         Take the key points and numerical descriptors ...   
simplify                                                           
relevance       Add 1-2 sentences to make this relevant for s...   

                                                               1  
article_title                                                NaN  
model                                                        NaN  
prompt                                                       NaN  
response_01                                                  NaN  
response_02                                                  NaN  
system_role                                                  NaN  
text                                                         NaN  
prep_step       Take the key points and numerical descriptors to  
task part 1                        Summarize for a LinkedIn post  
task part 2              Use terms a 12-year-old can understand.  
task part 3          Add 1-2 sentences to make this relevant for  
audience                                                 seniors  
prompt         Take the key points and numerical descriptors ...  
simplify                 Use terms a 12-year-old can understand.  
relevance       Add 1-2 sentences to make this relevant for s...

In [30]:
qna_chain_dict = simplify_chaining_dict(prompts_df, qna_chain_dict, chaining_dict[iteration_id], iteration_id,
    simplify_iteration=1
    )

text1_prompt00
	Simplifying response_01...
	...Prompt:  Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Simplifying response_02...
	...Prompt:  Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3


In [31]:
qna_chain_dict[iteration_id]

{'response_01': {0: {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma 

In [35]:
qna_chain_dict[iteration_id]['response_01']

{0: {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and ur

In [32]:
qna_chain_dict[iteration_id]['response_02']

{0: {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and ur

In [34]:
chaining_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [64]:
qna_chain_dict[7]

{'response_01': {0: {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma 

# Update prompts_df

In [40]:
# from itertools import product
# prompts_dict = dict()
experiment_num = 8

prep_step = [
    # "Take the key points to",
    "Take the key points and numerical descriptors to",
    # ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    # "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    # "lay audience",
    # "",
    "seniors",
    # "people who enjoy sports"
]
task_part2 = [
    "",
    "Use terms a 12-year-old can understand.",
    # "Assume your audience has no science background."
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    "Add 1-2 sentences to make this relevant for"
    # "Add 1-2 sentences to make this relevant for older adults."
    # "Once you are done, add 1-2 sentences to make this relevant for older adults.",
    ""
]

prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
    columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])

prompts_df = pd.DataFrame(product(prep_step, task_part1), 
    columns=['prep_step', 'task part 1'])


prompts_df['prompt'] = prompts_df.apply(
    lambda row: f"{row['prep_step']} {row['task part 1']}.", 
    axis=1)
# prompts_df['simplify'] = prompts_df.apply(
#     lambda row: f" {row['task part 2'] if row['task part 2'] else ''}", 
#     axis=1)
# prompts_df['relevance'] = prompts_df.apply(
#     lambda row: f" {row['task part 3']} {row['audience']} " if row['audience'] else '', 
#     axis=1) 
prompts_dict[experiment_num] = prompts_df
prompts_df

prep_step  \
0  Take the key points and numerical descriptors to   

                     task part 1  \
0  Summarize for a LinkedIn post   

                                                                            prompt  
0  Take the key points and numerical descriptors to Summarize for a LinkedIn post.

In [53]:
prompts_dict[6].transpose()

0  \
prep_step                                   Take the key points and numerical descriptors to   
task part 1                                                    Summarize for a LinkedIn post   
task part 2                                                                                    
task part 3                                      Add 1-2 sentences to make this relevant for   
audience                                                                             seniors   
prompt       Take the key points and numerical descriptors to Summarize for a LinkedIn post.   
simplify                                                                                       
relevance                               Add 1-2 sentences to make this relevant for seniors    

                                                                                           1  
prep_step                                   Take the key points and numerical descriptors to  
task part 1                                                    Summarize for a LinkedIn post  
task part 2                                          Use terms a 12-year-old can understand.  
task part 3                                      Add 1-2 sentences to make this relevant for  
audience                                                                             seniors  
prompt       Take the key points and numerical descriptors to Summarize for a LinkedIn post.  
simplify                                             Use terms a 12-year-old can understand.  
relevance                               Add 1-2 sentences to make this relevant for seniors

In [60]:
for key, value in prompts_dict[6].transpose().items():
    # print(dict({key: prompts_dict[6][key]}))
    # print(key, '\n\t', value)
    print(dict({key: value}))

{0: prep_step                                     Take the key points and numerical descriptors to
task part 1                                                      Summarize for a LinkedIn post
task part 2                                                                                   
task part 3                                        Add 1-2 sentences to make this relevant for
audience                                                                               seniors
prompt         Take the key points and numerical descriptors to Summarize for a LinkedIn post.
simplify                                                                                      
relevance                                 Add 1-2 sentences to make this relevant for seniors 
Name: 0, dtype: object}
{1: prep_step                                     Take the key points and numerical descriptors to
task part 1                                                      Summarize for a LinkedIn post
task part 2       

In [62]:
prompts_dict[6].transpose().apply(lambda x: x['prompt'])

0    Take the key points and numerical descriptors to Summarize for a LinkedIn post.
1    Take the key points and numerical descriptors to Summarize for a LinkedIn post.
dtype: object

# Iteration 8

In [67]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        self.simple_summary_dict['simplify_task'] = simplify_task
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    prompt_column='simplify', simplify_iteration=None):
    # qna_chain_dict[iteration_id] = dict()
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'{text_prompt_key}')
        summary_keys = [key for key in chaining_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[f'simplify_prompt{index}'] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict, pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except:
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 8
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()
qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)

# qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[iteration_id], iteration_id,
#     simplify_iteration=1
#     )

**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!


In [69]:
qna_dict[8]

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [70]:
task_part2

['', 'Use terms a 12-year-old can understand.']

In [72]:
simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[iteration_id], iteration_id,
    simplify_iteration=1
    )

text1_prompt00


KeyError: 'text1_prompt00'

## 8.2

In [73]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        self.simple_summary_dict['simplify_task'] = simplify_task
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    prompt_column='simplify', simplify_iteration=None):
    # qna_chain_dict[iteration_id] = dict()
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[f'simplify_prompt{index}'] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict, pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except:
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 8.2
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

# qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
#     iteration_id=iteration_id, n_choices=n_choices)

simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[8], iteration_id,
    simplify_iteration=1
    )

**text1_prompt00
	Simplifying response_01...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Simplifying response_02...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
Unable to concatenate simple summary DataFrame to original DataFrame


In [74]:
qna_dict[8.2]

{'simplify_prompt0': {'simplify_task': 'Use terms a 12-year-old can understand.',
  'simple_summary1_01': "Chronic pain is when someone has pain that lasts a long time and it can be really expensive to treat. Right now, the treatments we have don't always work because pain is really complicated. A study found that when women didn't drink enough water, they felt more pain, even if they were on their period. They could handle the pain for less time and it felt worse. Drinking water didn't make the pain go away, but it did help with feeling thirsty.",
  'simple_summary1_02': "Chronic pain is when someone has pain that lasts a long time and it can be a big problem for their health. The treatments we have now don't always work because pain is complicated. A study found that when women don't drink enough water, they can feel more pain. This happens because of changes in their body that happen when they don't drink enough water. The study showed that drinking water didn't make the pain go awa

In [76]:
pd.concat([qna_dict[8], pd.DataFrame(qna_dict[8.2])])

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p   
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                gpt-3.5-turbo   
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

## 8.3

In [77]:
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        self.simple_summary_dict['simplify_task'] = simplify_task
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    prompt_column='simplify', simplify_iteration=None):
    # qna_chain_dict[iteration_id] = dict()
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict, pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            print(error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 8.3
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

# qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
#     iteration_id=iteration_id, n_choices=n_choices)

simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[8], iteration_id,
    simplify_iteration=1
    )

**text1_prompt00
	Simplifying response_01...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Simplifying response_02...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
cannot concatenate object of type '<class 'dict'>'; only Series and DataFrame objs are valid
Unable to concatenate simple summary DataFrame to original DataFrame


# 8.4

In [87]:
import traceback
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        self.simple_summary_dict['simplify_task'] = simplify_task
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    prompt_column='simplify', simplify_iteration=None):
    # qna_chain_dict[iteration_id] = dict()
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            # print(error)
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 8.4
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

# qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
#     iteration_id=iteration_id, n_choices=n_choices)

simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[8], iteration_id,
    simplify_iteration=1
    )

**text1_prompt00
	Simplifying response_01...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Simplifying response_02...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
An error occurred on line 157 in C:\Users\silvh\AppData\Local\Temp\ipykernel_12104\2914826232.py : cannot concatenate object of type '<class 'dict'>'; only Series and DataFrame objs are valid
Unable to concatenate simple summary DataFrame to original DataFrame


In [82]:
qna_dict[8]

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [ ]:
qna_dict[8.4]

{0: {'simplify_task': 'Use terms a 12-year-old can understand.',
  'simple_summary1_01': "Chronic pain is when someone has pain that lasts a long time and it can be really expensive to treat. Right now, the treatments we have don't always work because pain is really complicated. A study found that when women didn't drink enough water, they felt more pain, even if they were on their period. They could handle the pain for less time and it felt worse. Drinking water didn't make the pain go away, but it did help with feeling thirsty.",
  'simple_summary1_02': "Chronic pain is when someone has pain that lasts a long time and it can be a big problem for their health. The treatments we have now don't always work because pain is complicated. A study found that when women don't drink enough water, they can feel more pain. This happens because of changes in their body that happen when they don't drink enough water. The study showed that drinking water didn't make the pain go away, but it did hel

In [84]:
pd.concat([qna_dict[8], pd.DataFrame(qna_dict[8.4])])

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

## 8.5

In [88]:
import traceback
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        self.simple_summary_dict['simplify_task'] = simplify_task
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None):
    # qna_chain_dict[iteration_id] = dict()
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            # print(error)
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 8.5
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

# qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
#     iteration_id=iteration_id, n_choices=n_choices)

simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[8], iteration_id,
    simplify_iteration=1, summary_iteration_id=8
    )

**text1_prompt00
	Simplifying response_01...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Simplifying response_02...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
Simple summaries added to original DataFrame


### review results
Rows are not in the expected order; system_role should be second row.

In [89]:
qna_dict[iteration_id]

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [90]:
qna_dict[iteration_id].drop(['prep_step', 'task part 1'])

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

# Iteration 9

In [91]:
import traceback
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        # self.qna['system_role'] = system_role
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        self.simple_summary_dict['simplify_task'] = simplify_task
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose().drop([prompt_column, 'system_role'])
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None):
    # qna_chain_dict[iteration_id] = dict()
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            # print(error)
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)

simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[8], iteration_id,
    simplify_iteration=1, summary_iteration_id=8
    )

**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
Error concatenating prompts DataFrame
**text1_prompt00
	Simplifying response_01...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Simplifying response_02...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
An error occurred on line 162 in C:\Users\silvh\AppData\Local\Temp\ipykernel_12104\2671024240.py : 8
Unable to concatenate simple summa

In [92]:
qna_dict[9]

{0: {'simplify_task': 'Use terms a 12-year-old can understand.',
  'simple_summary1_01': "Chronic pain is when someone has pain that lasts a long time and it can be really expensive to treat. Right now, the treatments we have don't always work because pain is really complicated. A study found that when women didn't drink enough water, they felt more pain, even if they were on their period. They could handle the pain for less time and it felt worse. Drinking water didn't make the pain go away, but it did help with feeling thirsty.",
  'simple_summary1_02': "Chronic pain is when someone has pain that lasts a long time and it can be a big problem for their health. The treatments we have now don't always work because pain is complicated. A study found that when women don't drink enough water, they can feel more pain. This happens because of changes in their hormones. The study showed that not drinking enough water made the pain worse and drinking water didn't make it better. We need to do 

In [93]:
simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[iteration_id], iteration_id,
    simplify_iteration=1
    )

**text1_prompt00
	Simplifying response_01...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	Simplifying response_02...
	...Prompt: Use terms a 12-year-old can understand.
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	Done creating prompt
	Sending request to GPT-3
		Requesting 1 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
An error occurred on line 162 in C:\Users\silvh\AppData\Local\Temp\ipykernel_12104\2671024240.py : cannot concatenate object of type '<class 'dict'>'; only Series and DataFrame objs are valid
Unable to concatenate simple summary DataFrame to original DataFrame


In [94]:
qna_dict[9]

{0: {'simplify_task': 'Use terms a 12-year-old can understand.',
  'simple_summary1_01': "Chronic pain is when someone has pain that lasts a long time and it can be really hard to treat. A new study found that not drinking enough water for a day can make the pain worse for women, no matter what time of the month it is. It made the pain feel more intense and unpleasant, and made it harder to tolerate. Drinking water right away didn't make the pain go away, but it did help with feeling thirsty. This means that it's important to make sure you drink enough water when you have chronic pain.",
  'simple_summary1_02': "Chronic pain is when someone has pain that lasts a long time and it can be a big problem for their health and how much money they have to spend. Right now, the treatments we have for chronic pain don't always work well. A new study found that when women don't drink enough water for a whole day, it can make their pain worse. Even if they're not on their period, their pain can be

## 9.2

In [98]:
import traceback
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        # self.qna['system_role'] = system_role
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose().drop([prompt_column, 'system_role'])
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None
    ):

    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            # print(error)
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9.2
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)



**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
Error concatenating prompts DataFrame


In [ ]:
import traceback
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        # self.qna['system_role'] = system_role
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose().drop([prompt_column, 'system_role'])
            ])
        except:
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None
    ):

    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            # print(error)
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9.2
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)



**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
Error concatenating prompts DataFrame


In [100]:
qna_dict

{1: {0: {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, an

## 9.3

In [106]:
import traceback
class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict()
        self.qna['article_title'] = title
        # self.qna['system_role'] = system_role
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna

    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            prompts_df = prompts_df.drop([prompt_column, 'system_role'])
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None
    ):

    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9.3
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)



**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
An error occurred on line 115 in C:\Users\silvh\AppData\Local\Temp\ipykernel_12104\2300954376.py : "['prompt', 'system_role'] not found in axis"
Error concatenating prompts DataFrame


In [109]:
qna_dict[iteration_id]

KeyError: 9.3

## 9.4

In [125]:
import traceback
# from collections import OrderedDict

class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() # use an ordered dictionary instead of a regular dictionary
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            prompts_df = prompts_df.drop([prompt_column, 'system_role'])
        except:
            pass
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None
    ):

    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9.4
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)



**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!


In [126]:
print(chaining_dict[iteration_id].keys())
chaining_dict[iteration_id]['text1_prompt00'].qna

dict_keys(['text1_prompt00'])


{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [131]:
pd.DataFrame(chaining_dict[iteration_id]['text1_prompt00'].qna, index=[0]).transpose()

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
system_role                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       You are an expert at science communication.
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [127]:
qna_dict[iteration_id]

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [119]:
print(type(qna_dict[iteration_id]))
qna_dict[iteration_id]

0
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           gpt-3.5-turbo
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

# Create new text_dict using abstract

In [136]:
test_text1 = """Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
 = 0.37) and increased ratings of pain intensity (by 0.7 ± 0.7 cm; P = 0.004; η2p
 = 0.55) and unpleasantness (by 0.7 ± 0.9 cm; P = 0.02; η2p
 = 0.40); these results were not influenced by menstrual phase. Water ingestion reduced thirst perception (visual analog scale, by 2.3 ± 0.9 cm; P < 0.001, η2p
 = 0.88) but did not reduce pain sensitivity. Therefore, hypohydration increases pain sensitivity in women with no influence of menstrual phase.
"""

test_text2 = """Daily Energy Expenditure through the Human Life Course

Total daily energy expenditure (“total expenditure”, MJ/d) reflects daily energy needs and is a critical variable in human health and physiology, yet it is unclear how daily expenditure changes over the life course. Here, we analyze a large, globally diverse database of total expenditure measured by the doubly labeled water method for males and females aged 8 days to 95 yr. We show that total expenditure is strongly related to fat free mass in a power-law manner and identify four distinct metabolic life stages. Fat free mass-adjusted daily expenditure accelerates rapidly in neonates (0-1yr) to ~46% above adult values at ~1 yr, declines slowly throughout childhood and adolescence (1-20 yr) to adult levels at ~20 yr, remains stable in adulthood (20-60 yr) even during pregnancy, and declines in older adults (60+ yr). These changes in total expenditure shed new light on human development and aging and should help shape nutrition and health strategies across the lifespan.
"""

test_text_dict = create_text_dict([test_text1, test_text2])
test_text_dict.keys()

dict_keys([1, 2])

### 9.42

In [137]:
iteration_id = 9.42
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)
qna_dict[iteration_id]

**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
**Text #2 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!


0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                       Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p   
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         gpt-3.5-turbo   
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [141]:
chaining_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine 

In [138]:
pd.DataFrame(chaining_dict[iteration_id]['text1_prompt00'].qna)

ValueError: If using all scalar values, you must pass an index

## Test Text

In [ ]:
test_text1 = """Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p

Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p
 = 0.37) and increased ratings of pain intensity (by 0.7 ± 0.7 cm; P = 0.004; η2p
 = 0.55) and unpleasantness (by 0.7 ± 0.9 cm; P = 0.02; η2p
 = 0.40); these results were not influenced by menstrual phase. Water ingestion reduced thirst perception (visual analog scale, by 2.3 ± 0.9 cm; P < 0.001, η2p
 = 0.88) but did not reduce pain sensitivity. Therefore, hypohydration increases pain sensitivity in women with no influence of menstrual phase.
"""

test_text2 = """Daily Energy Expenditure through the Human Life Course

Total daily energy expenditure (“total expenditure”, MJ/d) reflects daily energy needs and is a critical variable in human health and physiology, yet it is unclear how daily expenditure changes over the life course. Here, we analyze a large, globally diverse database of total expenditure measured by the doubly labeled water method for males and females aged 8 days to 95 yr. We show that total expenditure is strongly related to fat free mass in a power-law manner and identify four distinct metabolic life stages. Fat free mass-adjusted daily expenditure accelerates rapidly in neonates (0-1yr) to ~46% above adult values at ~1 yr, declines slowly throughout childhood and adolescence (1-20 yr) to adult levels at ~20 yr, remains stable in adulthood (20-60 yr) even during pregnancy, and declines in older adults (60+ yr). These changes in total expenditure shed new light on human development and aging and should help shape nutrition and health strategies across the lifespan.
"""

test_text_dict = create_text_dict([test_text1, test_text2])
test_text_dict.keys()

dict_keys([1, 2])

## 9.5

In [143]:
import traceback
# from collections import OrderedDict

class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() # use an ordered dictionary instead of a regular dictionary
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            prompts_df = prompts_df.drop([prompt_column, 'system_role'])
        except:
            pass
        print('temp_qna_dict index:', pd.DataFrame(temp_qna_dict[key]).index)
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None
    ):

    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9.5
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)



**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
temp_qna_dict index: Index(['article_title', 'model', 'prompt', 'response_01', 'response_02',
       'system_role', 'text'],
      dtype='object')
**Text #2 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
temp_qna_dict index: Index(['article_title', 'model', 'prompt', 'response_01', 'response_02',
       'system_role', 'text'],
      dtype='object')


In [144]:
qna_dict[iteration_id]

0  \
article_title                                                                                                                                                                                                                                                                                                                                                                                                                                                                       Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p   
model                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         gpt-3.5-turbo   
prompt                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

## Iteration 9.6

In [145]:
import traceback
from collections import OrderedDict

class Chaining:

    def __init__(self, text):
        self.text = text

    def summarize(self, task, model="gpt-3.5-turbo", temperature=0.7, n_choices=5, max_tokens=1000,
          text_key=['text_discussion'],
        system_role = "You are an expert at science communication."
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chatbot class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chatbot(self.text,
            system_role=system_role, model=model, temperature=temperature, n_choices=n_choices,
            max_tokens=max_tokens
            )
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() # use an ordered dictionary instead of a regular dictionary
        self.qna['article_title'] = title
        self.qna['system_role'] = system_role
        self.qna['prompt'] = task
        self.qna['model'] = model
        self.summaries_dict = dict()
        self.article_title = title

        try:
            response = chatbot.gpt(prompt)
        except:
            print('\t**API request failed**')
            return self.qna, chatbot
        try:
            for index, choice in enumerate(response.choices):
                self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(r'response', rf'simple_summary{str(simplify_iteration)}', key)
            self.simplify_bot_dict[new_key] = Chatbot(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt).choices[0]["message"]["content"]
                print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna.update({'text': self.qna.pop('text')})
        return self.simple_summary_dict

def batch_summarize_chain(text_dict, prompts_df, qna_dict,  chatbot_dict, iteration_id, n_choices=5,
    prompt_column='prompt',
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prompts_df: DataFrame containing the prompts.
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    prompts_df = prompts_df.reset_index(drop=True)
    qna_dfs_list = []
    chatbot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = OrderedDict()
        for index, input in prompts_df[prompt_column].items():
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            try:
                chatbot = Chaining(text)
                temp_qna_dict[key][index] = chatbot.summarize(input, n_choices=n_choices)
                chatbot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
            except:
                print('\t...Error making chatbot request')
                break
        try:
            prompts_df = prompts_df.drop([prompt_column, 'system_role'])
        except:
            pass
        print('temp_qna_dict index:', pd.DataFrame(temp_qna_dict[key]).index)
        try:
            updated_qna_dict = pd.concat([
                pd.DataFrame(temp_qna_dict[key]),
                prompts_df.transpose()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chatbot_dict
        try:
            qna_dfs_list.append(updated_qna_dict)
            qna_dict[iteration_id] = pd.concat(qna_dfs_list, axis=1)
            if save_outputs:
                try:
                    append_version = append_version if filename else False
                    filename = filename if filename else f'{datetime.now().strftime("%Y-%m-%d_%H%M")}_prompt_experiments_{"{:02d}".format(iteration_id)}'
                    savepickle(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                    save_csv(qna_dict[iteration_id], filename=filename, path=pickle_path, append_version=append_version)
                except:
                    print('Unable to save outputs')
        except:
            print('Error concatenating DataFrames')
    return qna_dict, chatbot_dict

def simplify_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None,
    prompt_column='simplify', simplify_iteration=None
    ):

    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    simple_summaries_dict = dict()
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = [prompt for prompt in simplify_prompts if len(prompt) >1]
    for text_prompt_key in chaining_bot_dict:
        print(f'**{text_prompt_key}')
        summary_keys = [key for key in chaining_bot_dict[text_prompt_key].qna if 'response' in key]

        for summary_key in summary_keys:
            print(f'\tSimplifying {summary_key}...')
            for index, prompt in enumerate(simplify_prompts):
                print(f'\t...Prompt: {prompt}')
                simple_summaries_dict[index] = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
        try:
            temp_qna_chain_dict = pd.concat([qna_chain_dict[summary_iteration_id], pd.DataFrame(simple_summaries_dict)])
            qna_chain_dict[iteration_id] = temp_qna_chain_dict
            print('Simple summaries added to original DataFrame')
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to concatenate simple summary DataFrame to original DataFrame')
            qna_chain_dict[iteration_id] = simple_summaries_dict

    return qna_chain_dict



iteration_id = 9.6
n_choices = 2
# qna_dict = dict()
# qna_chain_dict = dict()
# chatbot_dict = dict()

qna_dict, chaining_dict = batch_summarize_chain(test_text_dict, prompts_df, qna_dict, chatbot_dict, 
    iteration_id=iteration_id, n_choices=n_choices)



**Text #1 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	**API request failed**
	...Success!
temp_qna_dict index: RangeIndex(start=0, stop=2, step=1)
**Text #2 prompt #0 of 0**
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	**API request failed**
	...Success!
temp_qna_dict index: RangeIndex(start=0, stop=2, step=1)


In [146]:
qna_dict[iteration_id]

0  \
0            {'article_title': 'Chronic pain is a pervasive health problem and is associated with tremendous socioeconomic costs. However, current pain treatments are often ineffective due, in part, to the multifactorial nature of pain. Mild hypohydration was shown to increase experimental pain sensitivity in men, but whether this also occurs in women has not been examined. Fluctuations in ovarian hormones (i.e., 17β-estradiol and progesterone) throughout the menstrual cycle may influence a woman’s pain sensitivity, as well as hydration levels, suggesting possible interactions between hypohydration and menstrual phase on pain. We investigated the effects of mild hypohydration (HYPO, 24 h of fluid restriction) on ischemic pain sensitivity in 14 eumenorrheic women during the early follicular (EF) and mid-luteal (ML) phases of their menstrual cycle. We also examined whether acute water ingestion could reverse the negative effects of hypohydration. Elevated serum osmolality, plasma copeptin, and urine specific gravity indicated mild hypohydration. Compared with euhydration, HYPO reduced pain tolerance (by 34 ± 46 s; P = 0.02, η2p', 'system_role': 'You are an expert at science communication.', 'prompt': 'Take the key points and numerical descriptors to Summarize for a LinkedIn post.', 'model': 'gpt-3.5-turbo'}   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         <summarization.Chatbot object at 0x0000026DE22E9CA0>   
prep_step                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     Take the key points and numerical descriptors to   
task 

In [ ]:
simplify_prompts = task_part2
qna_dict = simplify_chaining_dict(simplify_prompts, qna_dict, chaining_dict[iteration_id], iteration_id,
    simplify_iteration=1, summary_iteration_id=None
    )

# *End of Page*